## 🛍️ Proje Girişi: Olist Brezilya E-Ticaret Veri Seti Analizi

Bu projede, Brezilya’nın en büyük online pazar yerlerinden biri olan **Olist** tarafından sağlanan kapsamlı e-ticaret veri seti analiz edilmiştir. Kaggle'da yayınlanan *Brazilian E-Commerce Public Dataset*; müşteri bilgileri, sipariş süreçleri, ürün özellikleri, ödeme yöntemleri, lojistik performansı ve müşteri değerlendirmelerini içeren çok boyutlu bir veri kaynağı sunmaktadır.

Bu veri seti, gerçek bir e-ticaret platformunun uçtan uca tüm iş akışını takip etmeye olanak tanıdığı için analitik açıdan oldukça zengindir. Amacımız bu veriyi kullanarak:

- **Temel tanımlayıcı istatistikler** çıkarmak,
- Sipariş, ürün, ödeme ve teslimat süreçlerini incelemek,
- **Müşteri memnuniyeti dinamiklerini anlamak**,  
- Ve istatistiksel yöntemlerle **hipotez testleri / A/B testleri** uygulayarak iş açısından anlamlı içgörüler üretmektir.

Bu çalışma kapsamında özellikle üç temel soruya odaklandık:

1. **Teslimat süresi müşteri memnuniyetini etkiliyor mu?**  
2. **Ürün kategorileri arasında sipariş tutarları anlamlı şekilde farklı mı?**  
3. **Ödeme yöntemi, siparişin tamamlanma/tamamlanmama ihtimalini etkiliyor mu?**

Bu sorulara yanıt bulmak için veri setindeki yedi ana tablo bir araya getirilmiş, temizleme ve ön işleme adımları uygulanmış, ardından hem görselleştirme hem de istatistiksel analiz yöntemleri kullanılmıştır.

Sonuç olarak bu proje, bir e-ticaret platformunda operasyonel verilerin nasıl analiz edileceğini, müşteri davranışlarının nasıl yorumlanacağını ve veriye dayalı kararların nasıl üretileceğini göstermeyi amaçlamaktadır.


In [55]:
from google.colab import drive
drive.mount('/content/drive')


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [56]:
path = "/content/drive/MyDrive/proje/"


In [3]:
import pandas as pd

path = "/content/drive/MyDrive/proje/"
encoding = "ISO-8859-1"

customers   = pd.read_csv(path + "olist_customers_dataset.csv", encoding=encoding)
order_items = pd.read_csv(path + "olist_order_items_dataset.csv", encoding=encoding)
payments    = pd.read_csv(path + "olist_order_payments_dataset.csv", encoding=encoding)
reviews     = pd.read_csv(path + "olist_order_reviews_dataset.csv", encoding=encoding)
orders      = pd.read_csv(path + "olist_orders_dataset.csv", encoding=encoding)
products    = pd.read_csv(path + "olist_products_dataset.csv", encoding=encoding)
sellers     = pd.read_csv(path + "olist_sellers_dataset.csv", encoding=encoding)


In [4]:
import numpy as np
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns


In [5]:
import pandas as pd

# --- 1: Daima copy yap ---
orders_clean = orders.copy().reset_index(drop=True)

# --- 2: datetime dönüştür ---
orders_clean['order_purchase_timestamp'] = pd.to_datetime(
    orders_clean['order_purchase_timestamp'], errors='coerce'
)
orders_clean['order_delivered_customer_date'] = pd.to_datetime(
    orders_clean['order_delivered_customer_date'], errors='coerce'
)

# --- 3: teslimat süresi (gün) ---
orders_clean['delivery_time'] = (
    orders_clean['order_delivered_customer_date'] -
    orders_clean['order_purchase_timestamp']
).dt.days

# --- 4: kontrol ---
print("delivery_time info:")
print(orders_clean['delivery_time'].describe())


delivery_time info:
count    96476.000000
mean        12.094086
std          9.551746
min          0.000000
25%          6.000000
50%         10.000000
75%         15.000000
max        209.000000
Name: delivery_time, dtype: float64


## 1. Veri Keşfi ve Hazırlık
Bu bölümde Olist açık e-ticaret veri setindeki tüm tabloları içeri aktaracak ve her bir tablonun yapısını inceleyeceğiz.
Bunun amacı veri modelini anlamak, hangi tablonun hangi bilgiyi içerdiğini görmek ve ileride yapacağımız birleştime (join) ve analiz adımlarına hazırlık yapmaktır.


In [6]:
path = "/content/drive/MyDrive/proje/"
encoding = "ISO-8859-1"

customers   = pd.read_csv(path + "olist_customers_dataset.csv", encoding=encoding)
order_items = pd.read_csv(path + "olist_order_items_dataset.csv", encoding=encoding)
payments    = pd.read_csv(path + "olist_order_payments_dataset.csv", encoding=encoding)
reviews     = pd.read_csv(path + "olist_order_reviews_dataset.csv", encoding=encoding)
orders      = pd.read_csv(path + "olist_orders_dataset.csv", encoding=encoding)
products    = pd.read_csv(path + "olist_products_dataset.csv", encoding=encoding)
sellers     = pd.read_csv(path + "olist_sellers_dataset.csv", encoding=encoding)


### 1.1 Tabloların Yapısını İnceleme
Bu adımda her tabloya ait ilk 10 satırı görüntüleyerek tablonun hangi kolonları içerdiğini ve genel yapısını anlamaya çalışacağız.
Bu, veri setini zihinsel olarak tanımamızı sağlar.






In [7]:
datasets = {
    "customers": customers,
    "order_items": order_items,
    "payments": payments,
    "reviews": reviews,
    "orders": orders,
    "products": products,
    "sellers": sellers
}

for name, df in datasets.items():
    print(f"\n========== {name.upper()} (first 10 rows) ==========\n")
    display(df.head(10))



========== CUSTOMERS (first 10 rows) ==========



customer_id                customer_unique_id  \
0  06b8999e2fba1a1fbc88172c00ba8bc7  861eff4711a542e4b93843c6dd7febb0   
1  18955e83d337fd6b2def6b18a428ac77  290c77bc529b7ac935b93aa66c333dc3   
2  4e7b3e00288586ebd08712fdd0374a03  060e732b5b29e8181a18229c7b0b2b5e   
3  b2b6027bc5c5109e529d4dc6358b12c3  259dac757896d24d7702b9acbbff3f3c   
4  4f2d8ab171c80ec8364f7c12e35b23ad  345ecd01c38d18a9036ed96c73b8d066   
5  879864dab9bc3047522c92c82e1212b8  4c93744516667ad3b8f1fb645a3116a4   
6  fd826e7cf63160e536e0908c76c3f441  addec96d2e059c80c30fe6871d30d177   
7  5e274e7a0c3809e14aba7ad5aae0d407  57b2a98a409812fe9618067b6b8ebe4f   
8  5adf08e34b2e993982a47070956c5c65  1175e95fb47ddff9de6b2b06188f7e0d   
9  4b7139f34592b3a31687243a302fa75b  9afe194fb833f79e300e37e580171f22   

   customer_zip_code_prefix          customer_city customer_state  
0                     14409                 franca             SP  
1                      9790  sao bernardo do campo             SP  
2                      1151              sao paulo             SP  
3                      8775        mogi das cruzes             SP  
4                     13056               campinas             SP  
5                     89254         jaragua do sul             SC  
6                      4534              sao paulo             SP  
7                     35182                timoteo             MG  
8                     81560               curitiba             PR  
9                     30575         belo horizonte             MG


========== ORDER_ITEMS (first 10 rows) ==========



order_id  order_item_id  \
0  00010242fe8c5a6d1ba2dd792cb16214              1   
1  00018f77f2f0320c557190d7a144bdd3              1   
2  000229ec398224ef6ca0657da4fc703e              1   
3  00024acbcdf0a6daa1e931b038114c75              1   
4  00042b26cf59d7ce69dfabb4e55b4fd9              1   
5  00048cc3ae777c65dbb7d2a0634bc1ea              1   
6  00054e8431b9d7675808bcb819fb4a32              1   
7  000576fe39319847cbb9d288c5617fa6              1   
8  0005a1a1728c9d785b8e2b08b904576c              1   
9  0005f50442cb953dcd1d21e1fb923495              1   

                         product_id                         seller_id  \
0  4244733e06e7ecb4970a6e2683c13e61  48436dade18ac8b2bce089ec2a041202   
1  e5f2d52b802189ee658865ca93d83a8f  dd7ddc04e1b6c2c614352b383efe2d36   
2  c777355d18b72b67abbeef9df44fd0fd  5b51032eddd242adc84c38acab88f23d   
3  7634da152a4610f1595efa32f14722fc  9d7a1d34a5052409006425275ba1c2b4   
4  ac6c3623068f30de03045865e4e10089  df560393f3a51e74553ab94004ba5c87   
5  ef92defde845ab8450f9d70c526ef70f  6426d21aca402a131fc0a5d0960a3c90   
6  8d4f2bb7e93e6710a28f34fa83ee7d28  7040e82f899a04d1b434b795a43b4617   
7  557d850972a7d6f792fd18ae1400d9b6  5996cddab893a4652a15592fb58ab8db   
8  310ae3c140ff94b03219ad0adc3c778f  a416b6a846a11724393025641d4edd5e   
9  4535b0e1091c278dfd193e5a1d63b39f  ba143b05f0110f0dc71ad71b4466ce92   

   shipping_limit_date   price  freight_value  
0  2017-09-19 09:45:35   58.90          13.29  
1  2017-05-03 11:05:13  239.90          19.93  
2  2018-01-18 14:48:30  199.00          17.87  
3  2018-08-15 10:10:18   12.99          12.79  
4  2017-02-13 13:57:51  199.90          18.14  
5  2017-05-23 03:55:27   21.90          12.69  
6  2017-12-14 12:10:31   19.90          11.85  
7  2018-07-10 12:30:45  810.00          70.75  
8  2018-03-26 18:31:29  145.95          11.65  
9  2018-07-06 14:10:56   53.99          11.40


========== PAYMENTS (first 10 rows) ==========



...

order_id                       customer_id  \
0  e481f51cbdc54678b7cc49136f2d6af7  9ef432eb6251297304e76186b10a928d   
1  53cdb2fc8bc7dce0b6741e2150273451  b0830fb4747a6c6d20dea0b8c802d7ef   
2  47770eb9100c2d0c44946d9cf07ec65d  41ce2a54c0b03bf3443c3d931a367089   
3  949d5b44dbf5de918fe9c16f97b45f8a  f88197465ea7920adcdbec7375364d82   
4  ad21c59c0840e6cb83a9ceb5573f8159  8ab97904e6daea8866dbdbc4fb7aad2c   
5  a4591c265e18cb1dcee52889e2d8acc3  503740e9ca751ccdda7ba28e9ab8f608   
6  136cce7faa42fdb2cefd53fdc79a6098  ed0271e0b7da060a393796590e7b737a   
7  6514b8ad8028c9f2cc2374ded245783f  9bdf08b4b3b52b5526ff42d37d47f222   
8  76c6e866289321a7c93b82b54852dc33  f54a9f0e6b351c431402b8461ea51999   
9  e69bfb5eb88e0ed6a785585b27e16dbf  31ad1d1b63eb9962463f764d4e6e0c9d   

  order_status order_purchase_timestamp    order_approved_at  \
0    delivered      2017-10-02 10:56:33  2017-10-02 11:07:15   
1    delivered      2018-07-24 20:41:37  2018-07-26 03:24:27   
2    delivered      2018-08-08 08:38:49  2018-08-08 08:55:23   
3    delivered      2017-11-18 19:28:06  2017-11-18 19:45:59   
4    delivered      2018-02-13 21:18:39  2018-02-13 22:20:29   
5    delivered      2017-07-09 21:57:05  2017-07-09 22:10:13   
6     invoiced      2017-04-11 12:22:08  2017-04-13 13:25:17   
7    delivered      2017-05-16 13:10:30  2017-05-16 13:22:11   
8    delivered      2017-01-23 18:29:09  2017-01-25 02:50:47   
9    delivered      2017-07-29 11:55:02  2017-07-29 12:05:32   

  order_delivered_carrier_date order_delivered_customer_date  \
0          2017-10-04 19:55:00           2017-10-10 21:25:13   
1          2018-07-26 14:31:00           2018-08-07 15:27:45   
2          2018-08-08 13:50:00           2018-08-17 18:06:29   
3          2017-11-22 13:39:59           2017-12-02 00:28:42   
4          2018-02-14 19:46:34           2018-02-16 18:17:02   
5          2017-07-11 14:58:04           2017-07-26 10:57:55   
6                          NaN                           NaN   
7          2017-05-22 10:07:46           2017-05-26 12:55:51   
8          2017-01-26 14:16:31           2017-02-02 14:08:10   
9          2017-08-10 19:45:24           2017-08-16 17:14:30   

  order_estimated_delivery_date  
0           2017-10-18 00:00:00  
1           2018-08-13 00:00:00  
2           2018-09-04 00:00:00  
3           2017-12-15 00:00:00  
4           2018-02-26 00:00:00  
5           2017-08-01 00:00:00  
6           2017-05-09 00:00:00  
7           2017-06-07 00:00:00  
8           2017-03-06 00:00:00  
9           2017-08-23 00:00:00


========== PRODUCTS (first 10 rows) ==========



product_id  product_category_name  \
0  1e9e8ef04dbcff4541ed26657ea517e5             perfumaria   
1  3aa071139cb16b67ca9e5dea641aaa2f                  artes   
2  96bd76ec8810374ed1b65e291975717f          esporte_lazer   
3  cef67bcfe19066a932b7673e239eb23d                  bebes   
4  9dc1a7de274444849c219cff195d0b71  utilidades_domesticas   
5  41d3672d4792049fa1779bb35283ed13  instrumentos_musicais   
6  732bd381ad09e530fe0a5f457d81becb             cool_stuff   
7  2548af3e6e77a690cf3eb6368e9ab61e       moveis_decoracao   
8  37cc742be07708b53a98702e77a21a02       eletrodomesticos   
9  8c92109888e8cdf9d66dc7e463025574             brinquedos   

   product_name_lenght  product_description_lenght  product_photos_qty  \
0                 40.0                       287.0                 1.0   
1                 44.0                       276.0                 1.0   
2                 46.0                       250.0                 1.0   
3                 27.0                       261.0                 1.0   
4                 37.0                       402.0                 4.0   
5                 60.0                       745.0                 1.0   
6                 56.0                      1272.0                 4.0   
7                 56.0                       184.0                 2.0   
8                 57.0                       163.0                 1.0   
9                 36.0                      1156.0                 1.0   

   product_weight_g  product_length_cm  product_height_cm  product_width_cm  
0             225.0               16.0               10.0              14.0  
1            1000.0               30.0               18.0              20.0  
2             154.0               18.0                9.0              15.0  
3             371.0               26.0                4.0              26.0  
4             625.0               20.0               17.0              13.0  
5             200.0               38.0                5.0              11.0  
6           18350.0               70.0               24.0              44.0  
7             900.0               40.0                8.0              40.0  
8             400.0               27.0               13.0              17.0  
9             600.0               17.0               10.0              12.0


========== SELLERS (first 10 rows) ==========



seller_id  seller_zip_code_prefix  \
0  3442f8959a84dea7ee197c632cb2df15                   13023   
1  d1b65fc7debc3361ea86b5f14c68d2e2                   13844   
2  ce3ad9de960102d0677a81f5d0bb7b2d                   20031   
3  c0f3eea2e14555b6faeea3dd58c1b1c3                    4195   
4  51a04a8a6bdcb23deccc82b0b80742cf                   12914   
5  c240c4061717ac1806ae6ee72be3533b                   20920   
6  e49c26c3edfa46d227d5121a6b6e4d37                   55325   
7  1b938a7ec6ac5061a66a3766e0e75f90                   16304   
8  768a86e36ad6aae3d03ee3c6433d61df                    1529   
9  ccc4bbb5f32a6ab2b7066a4130f114e3                   80310   

         seller_city seller_state  
0           campinas           SP  
1         mogi guacu           SP  
2     rio de janeiro           RJ  
3          sao paulo           SP  
4  braganca paulista           SP  
5     rio de janeiro           RJ  
6             brejao           PE  
7          penapolis           SP  
8          sao paulo           SP  
9           curitiba           PR

Yukarıdaki çıktılar, her tablonun genel yapısını göstermektedir.
Bu yapı bize hangi tabloların hangi anahtarlarla bağlanabileceğini ve hangi analizlerin hangi tablolardan yapılacağını göstermeye yardımcı olur.
Bir sonraki adımda her tablonun kolon bilgilerini ve eksik değer durumlarını inceleyeceğiz.


### 1.2 Tabloların Kolon Yapısı ve Eksik Değer Analizi

Bu aşamada her tablonun:
- kolon isimlerini
- veri tiplerini
- eksik değer sayılarını

inceleyerek veri bütünlüğünü değerlendireceğiz.

Bu adım; modelleme, join'ler ve hipotez testleri öncesinde çok kritiktir.


In [8]:
for name, df in datasets.items():
    print(f"\n========== {name.upper()} — COLUMN INFO ==========\n")

    # Kolon isimleri
    print("👉 Kolonlar:")
    print(df.columns.tolist())

    # Veri tipleri
    print("\n👉 Veri Tipleri:")
    print(df.info())

    # Eksik değer sayıları
    print("\n👉 Eksik Değer Sayıları:")
    print(df.isnull().sum())

    print("\n------------------------------------------------------\n")



========== CUSTOMERS — COLUMN INFO ==========

👉 Kolonlar:
['customer_id', 'customer_unique_id', 'customer_zip_code_prefix', 'customer_city', 'customer_state']

👉 Veri Tipleri:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 99441 entries, 0 to 99440
Data columns (total 5 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   customer_id               99441 non-null  object
 1   customer_unique_id        99441 non-null  object
 2   customer_zip_code_prefix  99441 non-null  int64 
 3   customer_city             99441 non-null  object
 4   customer_state            99441 non-null  object
dtypes: int64(1), object(4)
memory usage: 3.8+ MB
None

👉 Eksik Değer Sayıları:
customer_id                 0
customer_unique_id          0
customer_zip_code_prefix    0
customer_city               0
customer_state              0
dtype: int64

------------------------------------------------------


========== ORDER_ITEMS — COLUMN INF

### 1.3 Eksik Değer Analizi ve Temizleme Stratejisi

Yaptığımız kolon incelemesi sonucunda tabloların eksik değer durumları şu şekildedir:

#### ✔ Reviews Tablosu
- `review_comment_message`: 52,847 adet eksik → Kullanıcı yorum yapmamış.
- Bu kolon isteğe bağlı bir metin olduğu için eksik kalması doğaldır.
- Çözüm: Bu kolonu analizlerimizde kullanmayacaksak olduğu gibi bırakabiliriz.

#### ✔ Orders Tablosu
- `order_delivered_carrier_date`: 1,783 eksik → Sipariş kargoya verilmemiş olabilir.
- `order_delivered_customer_date`: 1,865 eksik → Sipariş teslim edilmemiş olabilir.
- Temizleme Stratejisi:
  - Teslimat süresi hesaplanacaksa, teslim edilmeyen siparişleri filtreleyerek çıkaracağız.
  - Hipotez testlerinde yalnızca tamamlanan siparişleri kullanacağız.

#### ✔ Products Tablosu
- `product_name_lenght`, `product_description_lenght`, `product_photos_qty`: 610 eksik → Bazı ürünlerde açıklama veya fotoğraf verilmemiş.
- `product_weight_g`, `product_length_cm`, `product_height_cm`, `product_width_cm`: 2 adet eksik → Çok küçük, doldurmak yerine drop yapılabilir.

#### 📌 Sonuç:
Eksik değerler genel olarak:
- **yorum metinleri**,
- **tamamlanmamış siparişler**
- **açıklaması olmayan ürünler**

kategorilerinde yoğunlaşmaktadır. Temizleme adımında bu kolonlar için uygun işlem uygulanacaktır.


In [9]:
# Reviews tablosu
# Yorum metni boş olabilir, bu tabloyu bozmadan bırakıyoruz
reviews_clean = reviews.copy()

# Orders tablosu
# Teslim edilmeyen siparişleri çıkarıyoruz (hipotez ve teslimat analizi için)
orders_clean = orders.dropna(subset=["order_delivered_customer_date"])

# Products tablosu
# 2 adet eksik fiziksel ölçü -> drop
products_clean = products.dropna(subset=["product_weight_g", "product_length_cm",
                                         "product_height_cm", "product_width_cm"])

# Genel eksik veri kontrolü
print("Orders Clean Shape:", orders_clean.shape)
print("Products Clean Shape:", products_clean.shape)
print("Reviews Clean Shape:", reviews_clean.shape)


Orders Clean Shape: (96476, 8)
Products Clean Shape: (32949, 9)
Reviews Clean Shape: (99224, 7)


Yukarıdaki temizlik adımları ile:

- Teslimat süresi hesaplamasında problem çıkarabilecek kayıtlar kaldırıldı.
- Ürün fiziksel ölçüleri eksik olan 2 satır düşürüldü.
- Yorum metni eksiklikleri doğal olduğu için dokunulmadı.

Artık temizlenmiş veri ile güvenilir analizlere geçmeye hazırız.


## 2. Tanımlayıcı İstatistikler

Bu bölümde Olist veri setindeki temel değişkenler için tanımlayıcı istatistikleri inceleyeceğim:
- Sipariş fiyatları
- Ürün kategorisi dağılımı
- Ödeme yöntemi dağılımı
- Teslimat süresi istatistikleri
- Müşteri memnuniyet puanları

Amaç, veri setinin genel yapısını ve öne çıkan desenleri anlamak.


In [10]:
import plotly.express as px
import numpy as np

# 1) Sipariş bazında toplam fiyat kolonu oluştur (ürün + kargo)
order_items['total_price'] = order_items['price'] + order_items['freight_value']

order_prices = (
    order_items
    .groupby('order_id', as_index=False)['total_price']
    .sum()
    .rename(columns={'total_price': 'order_total_price'})
)

# 2) Temel istatistikler
mean_price   = order_prices['order_total_price'].mean()
median_price = order_prices['order_total_price'].median()
std_price    = order_prices['order_total_price'].std()

print("Ortalama sipariş fiyatı:", round(mean_price, 2))
print("Medyan sipariş fiyatı :", round(median_price, 2))
print("Std sapma            :", round(std_price, 2))

# 3) Histogram
fig = px.histogram(
    order_prices,
    x='order_total_price',
    nbins=50,
    title='Sipariş Toplam Fiyat Dağılımı'
)
fig.show()


Ortalama sipariş fiyatı: 160.58
Medyan sipariş fiyatı : 105.29
Std sapma            : 220.47


In [11]:
product_counts = (
    products_clean['product_category_name']
    .value_counts()
    .head(15)
    .reset_index()
)

# Kolonları manuel olarak düzenleyelim
product_counts.columns = ['product_category_name', 'count']

print(product_counts.head())

fig = px.bar(
    product_counts,
    x='product_category_name',
    y='count',
    title='En Çok Ürüne Sahip İlk 15 Kategori',
    labels={'product_category_name': 'Ürün Kategorisi', 'count': 'Ürün Sayısı'}
)

fig.update_layout(xaxis_tickangle=-45)
fig.show()


   product_category_name  count
0        cama_mesa_banho   3029
1          esporte_lazer   2867
2       moveis_decoracao   2657
3           beleza_saude   2444
4  utilidades_domesticas   2335


In [12]:
payment_counts = payments['payment_type'].value_counts().reset_index()
payment_counts.columns = ['payment_type', 'count']

fig = px.pie(
    payment_counts,
    names='payment_type',
    values='count',
    title='Ödeme Yöntemi Dağılımı'
)
fig.show()


In [13]:
# Tarih kolonlarını datetime'e dönüştür
orders_clean['order_purchase_timestamp'] = pd.to_datetime(orders_clean['order_purchase_timestamp'], errors='coerce')
orders_clean['order_delivered_customer_date'] = pd.to_datetime(orders_clean['order_delivered_customer_date'], errors='coerce')



# Teslimat süresi (gün)
orders_clean = orders_clean.copy()
orders_clean['delivery_time'] = (
    orders_clean['order_delivered_customer_date'] - orders_clean['order_purchase_timestamp']
).dt.days

# Temel istatistikler
delivery_desc = orders_clean['delivery_time'].describe()
print(delivery_desc)

# Histogram
fig = px.histogram(
    orders_clean,
    x='delivery_time',
    nbins=40,
    title='Teslimat Süresi Dağılımı (Gün)'
)
fig.show()

# Kutu grafiği
fig = px.box(
    orders_clean,
    y='delivery_time',
    title='Teslimat Süresi Kutu Grafiği'
)
fig.show()


count    96476.000000
mean        12.094086
std          9.551746
min          0.000000
25%          6.000000
50%         10.000000
75%         15.000000
max        209.000000
Name: delivery_time, dtype: float64


/tmp/ipython-input-434329157.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipython-input-434329157.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [14]:
# Temel istatistikler
print(reviews_clean['review_score'].describe())

# Memnuniyet oranı (4 ve 5 puan alanların oranı)
satisfied_ratio = (reviews_clean['review_score'] >= 4).mean()
print("Memnuniyet oranı (4-5 puan):", round(satisfied_ratio * 100, 2), "%")

# Puan dağılımı (bar)
score_counts = (
    reviews_clean['review_score']
    .value_counts()
    .sort_index()
    .reset_index(name='count')  # güvenli yöntem
)

score_counts.columns = ['review_score', 'count']  # kolonları netleştir

fig = px.bar(
    score_counts,
    x='review_score',
    y='count',
    title='Müşteri Memnuniyet Puan Dağılımı',
    labels={'review_score': 'Puan', 'count': 'Sipariş Sayısı'}
)

fig.show()




count    99224.000000
mean         4.086421
std          1.347579
min          1.000000
25%          4.000000
50%          5.000000
75%          5.000000
max          5.000000
Name: review_score, dtype: float64
Memnuniyet oranı (4-5 puan): 77.07 %


### 📊 Müşteri Memnuniyeti Puan Dağılımı Yorumu:
- En yüksek yoğunluk **5 puan** kategorisindedir; bu da müşterilerin genel olarak memnun olduğunu gösterir.
- **1 ve 2 puanların** toplamı yaklaşık %15 civarındadır; bu grup memnuniyetsiz müşterileri temsil eder.
- **3 puan** ise kararsız/orta seviyede memnuniyeti göstermektedir.
- Dağılım sağa çarpık (right-skewed) bir yapıya sahiptir; yani yüksek puanlar düşük puanlara göre çok daha fazladır.

Bu sonuç, müşteri deneyiminin genel olarak olumlu olduğunu, ancak düşük puan veren azımsanamayacak bir grubun da bulunduğunu ve bu grubun davranışlarının ayrıca incelenmesi gerektiğini göstermektedir.


## 🧮 Tanımlayıcı İstatistikler – Genel Özet

Bu bölümde Olist veri seti üzerinde temel tanımlayıcı istatistikler incelenmiş ve kullanıcı davranışlarına dair önemli bulgular elde edilmiştir.

---

### 📦 Sipariş Fiyatı Analizi
- **Ortalama sipariş fiyatı:** 160.58 BRL  
- **Medyan sipariş fiyatı:** 105.29 BRL  
- **Std sapma:** 220.47  
- Fiyat dağılımı **sağa çarpık** yapıdadır; düşük fiyatlı siparişler çoğunlukta, yüksek fiyatlı siparişler ise uzun bir kuyruk oluşturmaktadır.
- Bu durum e-ticarete özgü ‘çok satan ucuz ürün – az satan pahalı ürün’ dinamiğini yansıtır.

---

### 🏷️ Ürün Kategorisi Dağılımı
- En çok ürünün bulunduğu kategoriler:  
  **cama_mesa_banho**, **esporte_lazer**, **moveis_decoracao**, **beleza_saude**  
- Ürün çeşitliliği özellikle ev, spor ve dekorasyon kategorilerinde yoğunlaşmaktadır.
- Bu kategoriler platformun ana satış hacmini oluşturmaktadır.

---

### 💳 Ödeme Yöntemi Dağılımı
- **Kredi kartı** açık ara en çok kullanılan yöntemdir (%73.9).  
- Ardından **boleto (banka fişi)** %19 ile gelir.  
- Diğer yöntemlerin kullanım oranı oldukça düşüktür.
- Bu dağılım, müşterilerin büyük oranda taksit veya kart kolaylığını tercih ettiğini göstermektedir.

---

### 🚚 Teslimat Süresi Analizi
- Teslimat sürelerinin çoğu **0–20 gün** aralığındadır.
- Ancak 60 gün ve üzeri sürelerde **uç değerler** görülmektedir; bunlar gecikme kaynaklı anomalilerdir.
- Kutu grafiği, teslimat sürelerinde geniş bir varyasyon olduğunu ve sistemde bazı operasyonel gecikmeler bulunduğunu göstermektedir.

---

### 😊 Müşteri Memnuniyeti Analizi
- **Ortalama puan:** 4.08  
- **Memnuniyet oranı (4–5 puan):** %77.07  
- 5 puan alan sipariş sayısı en yüksek seviyededir.
- 1 ve 2 puanlar memnuniyetsizliği temsil eder ve toplamda yaklaşık %15 civarındadır.
- Genel müşteri deneyimi olumlu görünse de düşük puan veren kullanıcı profili ayrıca analiz edilmelidir.

---

### 🎯 Genel Değerlendirme
Bu analizler sonucunda Olist platformunda:
- Siparişlerin çoğu düşük fiyatlı,
- Ürün çeşitliliği ev/spor/dekorasyon kategorilerinde yoğun,
- Kullanıcıların büyük kısmı kredi kartı kullanıyor,
- Teslimat performansında bazı uzun gecikme outlier’ları mevcut,
- Müşteriler genel olarak memnun (%77 memnuniyet).

Bu bulgular bir sonraki aşamada hipotez testleri ve A/B analizleri için yol gösterici olacaktır.


## 3. Hipotez Testleri (A/B Testi)

Bu bölümde veri seti üzerinde müşteri davranışlarını ve satış performansını etkileyen değişkenleri incelemek için istatistiksel hipotez testleri uygulanmıştır.

Her bir test için:
- Hipotezler kurulmuş,
- Uygun istatistiksel test seçilmiş,
- Sonuçlar yorumlanmıştır.


🔵 3.1 Hipotez 1 — Teslimat Süresi Müşteri Memnuniyetini Etkiler mi? (T-testi)

🎯 Hipotez:

H0: Teslimat süresi, müşteri memnuniyetini etkilemez.  
H1: Daha hızlı teslim edilen siparişlerde memnuniyet daha yüksektir.

In [15]:
# Teslimat süresi olan siparişlerle yorumları birleştir
merged = orders_clean.merge(
    reviews_clean[['order_id', 'review_score']],
    on='order_id',
    how='inner'
)

# Hızlı teslim (median altı) ve yavaş teslim (median üstü) olarak iki gruba ayır
median_time = merged['delivery_time'].median()

fast = merged[merged['delivery_time'] <= median_time]['review_score']
slow = merged[merged['delivery_time'] > median_time]['review_score']

from scipy.stats import ttest_ind

t_stat, p_value = ttest_ind(fast, slow)
print("T-istatistiği:", t_stat)
print("p-değeri:", p_value)


T-istatistiği: 59.436355611408594
p-değeri: 0.0


# 📊 Teslimat Süresi Müşteri Memnuniyetini Etkiliyor mu?
## Hipotez Testi Sonuç Özeti

### 🎯 Amaç  
Siparişlerin **teslimat hızının**, müşterilerin bıraktığı **review_score** üzerinde anlamlı bir etkisi olup olmadığını test etmek.

---

## 🧪 1. Hipotezler

**H₀ (Null):** Teslimat süresi müşteri memnuniyetini etkilemez.  
**H₁ (Alternatif):** Daha hızlı teslim edilen siparişlerin memnuniyet puanı daha yüksektir.

---

## 🔧 2. Yöntem

- `orders_clean` ve `reviews_clean` tabloları **order_id** ile birleştirildi.  
- Teslimat süresinin **medyanı** hesaplandı.  
- Siparişler iki gruba ayrıldı:
  - **Hızlı Teslim** → teslim süresi medyanın altında  
  - **Yavaş Teslim** → teslim süresi medyanın üstünde  
- Her iki grubun `review_score` değerleri için **bağımsız örneklem T-testi (ttest_ind)** uygulandı.

---

## 📈 3. Test Sonuçları

- **T-istatistiği:** 59.43  
- **p-değeri:** 0.0000  

---

## ✅ 4. Yorum

p-değeri **0.05’ten çok küçük** olduğu için:

### ✔ H₀ reddedilir.  
### ✔ Teslimat süresi memnuniyeti anlamlı şekilde etkiler.

**Sonuç:**  
Hızlı teslim alan müşteriler, yavaş teslim alanlara göre anlamlı derecede daha yüksek memnuniyet puanı vermektedir.  
Bu durum lojistik süreçlerinin müşteri deneyimi üzerindeki kritik etkisini göstermektedir.

---


3.2 Hipotez 2 — Ürün Kategorisine Göre Sipariş Değeri Farklı mıdır? (ANOVA Testi)

🎯 Hipotez:

H0: Ürün kategorisine göre ortalama sipariş değeri farklı değildir.  
H1: En az bir kategori diğerlerinden anlamlı şekilde farklıdır.


In [16]:
# Sipariş toplam fiyatı
order_items['total_price'] = order_items['price'] + order_items['freight_value']

# Ürün kategorisini ekle
merged_cat = order_items.merge(
    products_clean[['product_id', 'product_category_name']],
    on='product_id',
    how='inner'
)

# ANOVA için kategorilere göre grupla
from scipy.stats import f_oneway

groups = [
    group['total_price'].values
    for name, group in merged_cat.groupby('product_category_name')
    if len(group) > 50  # çok küçük grupları ele
]

f_stat, p_value = f_oneway(*groups)
print("F-istatistiği:", f_stat)
print("p-değeri:", p_value)


F-istatistiği: 239.55385499109462
p-değeri: 0.0


## 🧪 Ürün Kategorileri Arasında Sipariş Değeri Farkı (ANOVA Testi)

Bu analizde, farklı ürün kategorilerindeki siparişlerin **ortalama toplam fiyatları arasında anlamlı bir fark olup olmadığını** test etmek için tek yönlü **ANOVA testi** uygulanmıştır.

---

### 🎯 Hipotezler

**H0 (Null):**  
Ürün kategorilerinin ortalama sipariş toplam değerleri arasında anlamlı bir fark yoktur.

**H1 (Alternatif):**  
En az bir ürün kategorisinin ortalama sipariş toplam değeri farklıdır.

---

### 🔍 Yöntem

- Siparişler için **total_price = price + freight_value** hesaplandı.  
- Ürün kategorisi bilgisi sipariş verisine eklendi.  
- ANOVA uygulanabilmesi için kategoriler:
  - `product_category_name` bazında gruplanmıştır.
  - Örnek sayısı 50’den az olan küçük kategoriler filtrelenmiştir.
- Her kategori için `total_price` değerleri teste dahil edilmiştir.

---

### 📊 ANOVA Test Sonuçları

- **F-istatistiği:** 239.55  
- **p-değeri:** 0.0  

---

### ✅ Sonuç ve Yorum

p-değeri **0.05’ten çok daha küçük** olduğundan:

➡ **H0 reddedilir.**

Bu, şu anlama gelir:

### ✔ Ürün kategorileri arasında ortalama sipariş toplam fiyatı açısından anlamlı fark vardır.

Bu farklılıklar:
- Fiyatlandırma stratejileri  
- Ürün tipleri ve maliyetleri  
- Lojistik/kargo bedelleri  
- Ürün çeşitliliği  

gibi nedenlerden kaynaklanıyor olabilir.

---

### 📌 Genel Yorum

Bu bulgu, e-ticaret analizlerinde:
- Segment bazlı fiyatlandırma,
- Kategori bazlı kampanya yönetimi,
- Talep analizi  

gibi karar süreçleri için kritik bir içgörüdür.


🟩 3.3 Hipotez 3 — Ödeme Yöntemi Tamamlanma Oranını Etkiler mi? (Ki-Kare Testi)

🎯 Hipotez:

H0: Ödeme yöntemi ile siparişin tamamlanma oranı arasında ilişki yoktur.  
H1: Farklı ödeme yöntemleri farklı tamamlanma oranlarına sahiptir.


In [17]:
# Orders tablosundan teslim bilgisi (delivered / not delivered)
orders['delivered_flag'] = orders['order_status'].isin(['delivered']).astype(int)

# Payments tablosu ile orders tablosunu birleştir
payments_status = payments.merge(
    orders[['order_id', 'delivered_flag']],
    on='order_id',
    how='inner'
)

# Çapraz tablo
contingency = pd.crosstab(
    payments_status['payment_type'],
    payments_status['delivered_flag']
)

print(contingency)

# Ki-kare testi
from scipy.stats import chi2_contingency
chi2, p_value, dof, expected = chi2_contingency(contingency)

print("Chi2:", chi2)
print("p-değeri:", p_value)


delivered_flag     0      1
payment_type               
boleto           593  19191
credit_card     2209  74586
debit_card        43   1486
not_defined        3      0
voucher          282   5493
Chi2: 170.81332506087486
p-değeri: 6.996888867827184e-36


### 📌 Hipotez Testi — Ödeme Yöntemi ve Teslim Edilme Durumu (Ki-Kare Testi)

#### 🎯 Amaç
Ödeme yönteminin siparişin teslim edilip edilmemesi üzerinde etkisi olup olmadığını incelemek.

#### 🧪 Hipotezler
- **H0:** Ödeme yöntemi ile teslim edilme durumu arasında ilişki yoktur.  
- **H1:** Ödeme yöntemi ile teslim edilme durumu arasında ilişki vardır.

#### 📊 Kontenjans Tablosu

payment_type | Teslim Edilmedi (0) | Teslim Edildi (1)
-------------|---------------------|-------------------
boleto       | 593                 | 19191
credit_card  | 2209                | 74586
debit_card   | 43                  | 1486
not_defined  | 3                   | 0
voucher      | 282                 | 5493

#### 📈 Ki-Kare Testi Sonuçları
- **Chi²:** 170.81332506807486  
- **p-değeri:** 6.996888867827184e-36  

#### 🧠 Sonuç ve Yorum
p-değeri **0.05’ten çok daha küçük** → **H0 reddedilir.**

➡ Ödeme yöntemi ile siparişin teslim edilme durumu arasında istatistiksel olarak anlamlı bir ilişki vardır.  
➡ Bazı ödeme yöntemleri (özellikle boleto ve voucher) diğer yöntemlere göre daha yüksek teslim edilmeme oranına sahiptir.


✅ 4. ADIM — GÖRSELLEŞTİRME ve YORUMLAMA

Aşağıdaki üç hipotez için görselleştirme yapacağız:

Teslimat Süresi → Memnuniyet (t-testi)

Ürün Kategorisi → Sipariş Değeri (ANOVA)

Ödeme Yöntemi → Teslim Edilme Durumu (Ki-Kare)

🎯 4.1 Teslimat Süresi ve Memnuniyet — Görselleştirme

In [18]:
import plotly.express as px

# Hızlı vs Yavaş teslim memnuniyet ortalamaları
mem_df = merged[['delivery_time', 'review_score']].copy()  # <-- önemli

# Bool değer üret
mem_df['group'] = mem_df['delivery_time'] <= median_time

# Bool → String dönüşümü (UYARIYI ÇÖZEN KISIM)
mem_df['group'] = mem_df['group'].astype(str)      # bool → string
mem_df['group'] = mem_df['group'].replace({
    'True': 'Hızlı Teslim',
    'False': 'Yavaş Teslim'
})

fig = px.box(
    mem_df,
    x='group',
    y='review_score',
    color='group',
    title='Teslimat Hızına Göre Müşteri Memnuniyeti',
    labels={'group': 'Teslimat Grubu', 'review_score': 'Puan'}
)
fig.show()




### 📊 Teslimat Süresi ve Memnuniyet — Görselleştirme

Aşağıdaki kutu grafiği, hızlı (medyan altı) ve yavaş (medyan üstü) teslim grubundaki müşteri memnuniyet puanlarını karşılaştırmaktadır.

- Hızlı teslim grubunun memnuniyet puanları genel olarak daha yüksektir.
- Yavaş teslim grubunda memnuniyet belirgin şekilde düşmektedir.
- Bu görsel, t-testinde elde ettiğimiz **p < 0.05** sonucunu desteklemektedir.

➡ **Sonuç:** Daha hızlı teslimat, anlamlı şekilde daha yüksek memnuniyet sağlar.


🎯 4.2 Ürün Kategorisi ve Sipariş Değeri — Görselleştirme (ANOVA)

In [19]:
fig = px.box(
    merged_cat,
    x='product_category_name',
    y='total_price',
    title='Kategori Bazında Sipariş Değerleri Dağılımı',
    labels={'product_category_name': 'Kategori', 'total_price': 'Sipariş Değeri'}
)
fig.update_layout(xaxis_tickangle=-45)
fig.show()


### 📊 Ürün Kategorisine Göre Sipariş Değerlerinin Görselleştirilmesi (ANOVA)

Kutugrafiği farklı ürün kategorilerinin sipariş tutarlarını karşılaştırmaktadır.

- Kategoriler arasında büyük fiyat farklılıkları gözlemlenmektedir.
- Bazı kategoriler (ör. elektronik, mobilya) çok daha yüksek fiyat aralığına sahiptir.
- Bu görsel, ANOVA analizinde elde edilen **p < 0.05** sonucunu desteklemektedir.

➡ **Sonuç:** Ürün kategorileri sipariş değerleri açısından anlamlı farklılık göstermektedir.


🎯 4.3 Ödeme Yöntemi ve Teslim Edilme Durumu — Görselleştirme (Ki-Kare)

In [20]:
import pandas as pd
import plotly.express as px

# teslim edilme oranları tablosu
delivery_rate = contingency.apply(lambda col: col / col.sum())

fig = px.bar(
    delivery_rate,
    barmode='group',
    title='Ödeme Yöntemine Göre Teslim Edilme Oranları',
    labels={'value': 'Oran', 'payment_type': 'Ödeme Yöntemi'}
)
fig.show()


### 📊 Ödeme Yöntemine Göre Teslim Edilme Oranları (Ki-Kare Testi)

Bu grafik, ödeme yöntemlerine göre teslim edilme oranlarını göstermektedir.

- Bazı ödeme yöntemlerinde teslim edilmeme oranı belirgin şekilde daha yüksektir.
  - **boleto** ve **voucher** kullanılan siparişlerde sorun oranı daha yüksek.
  - **credit_card** ile verilen siparişlerde teslim problemleri çok daha az.
- Bu görsel, Ki-Kare testinde elde ettiğimiz çok düşük p-değeri ile uyumludur.

➡ **Sonuç:** Ödeme yöntemi ile teslim edilme durumu arasında anlamlı bir ilişki vardır.


## 🧾 5. Sonuç ve Sonraki Adımlar

### 📌 Genel Bulguların Özeti

Bu proje kapsamında Olist e-ticaret veri seti üzerinde hem tanımlayıcı analizler hem de istatistiksel hipotez testleri uyguladık. Çıkan önemli bulgular:

#### 🛒 Sipariş Fiyatları
- Ortalama sipariş değeri **~160₺**, medyan ise **~105₺**.
- Fiyat dağılımı sağa çarpık; birkaç çok yüksek tutarlı sipariş ortalamayı yukarı çekiyor.

#### 🧂 Ürün Kategorileri
- En çok ürün bulunan kategoriler: **cama_mesa_banho**, **esporte_lazer**, **moveis_decoracao**.
- Kategoriler arasında ürün çeşitliliği oldukça yüksek.

#### 💳 Ödeme Yöntemleri
- En çok kullanılan yöntem açık ara **kredi kartı (%73.9)**.
- Boleto ve voucher gibi yöntemler daha az kullanılıyor.

#### 🚚 Teslimat Süreleri
- Teslimat süresi ortalamada **10–12 gün**, fakat bazı aykırı değerlerde 100 günün üzerine çıkıyor.
- Teslimat süresi dağılımı uzun kuyruklu (right-skewed).

#### ⭐ Müşteri Memnuniyeti
- Ortalama memnuniyet puanı **4.08**.
- Müşterilerin **%77’si (4–5 puan)** memnun.

---

### 📊 İstatistiksel Test Sonuçları

#### 📌 1. Teslimat Süresi → Memnuniyet (T-Testi)
- **p-değeri = 0.0 → anlamlı fark var.**
- Hızlı teslim alan müşteriler anlamlı derecede daha yüksek memnuniyet bildiriyor.

➡ *Teslimatı hızlandırmak memnuniyeti artırır.*

---

#### 📌 2. Ürün Kategorisi → Sipariş Değeri (ANOVA)
- **p-değeri = 0.0 → kategoriler arasında anlamlı fark var.**
- Bazı kategorilerde sipariş tutarları çok daha yüksek.

➡ *Kategori bazlı fiyat analitiği ve segmentleme yapılabilir.*

---

#### 📌 3. Ödeme Yöntemi → Teslim Edilme Durumu (Ki-Kare)
- **p-değeri ≈ 6.99e-36 → anlamlı ilişki var.**
- Boleto ve voucher ile verilen siparişlerde teslim edilmeme oranı daha yüksek.

➡ *Riskli ödeme yöntemleri için ek doğrulama ve takip stratejisi gerekli.*

---

### 🔮 Sonraki Adımlar (Öneriler)

1. **Teslimat optimizasyonu**
   - Yavaş teslimat bölgeleri haritalandırılabilir.
   - En problemli lojistik ortakları tespit edilebilir.

2. **Kategori bazlı fiyat stratejileri**
   - Yüksek değerli kategoriler için özel kampanyalar ve fırsatlar uygulanabilir.

3. **Ödeme yöntemi risk analizi**
   - Boleto/voucher siparişleri için ek güvenlik ve takip adımları eklenebilir.
   - Ödeme yöntemine göre tahmini teslim başarısı modeli geliştirilebilir.

4. **Müşteri memnuniyeti modellemesi**
   - Memnuniyet puanı için makine öğrenmesi modeli kurulabilir.
   - "Müşteri kaybı (churn)" erken tahmin modeli oluşturulabilir.

5. **Dashboard oluşturma**
   - Power BI veya Looker Studio ile yönetime sunulacak bir iş zekası paneli hazırlanabilir.

---

### ✔ Genel Sonuç

Bu analiz, Olist platformunda **teslimat süresi, ödeme yöntemi ve ürün kategorisinin**, hem müşteri memnuniyetini hem de operasyonel kaliteyi etkileyen temel faktörler olduğunu göstermektedir. Çıkan sonuçlar, e-ticaret operasyonlarının iyileştirilmesi için güçlü içgörüler sunmaktadır.






## 📘 Ek Bölüm:


### 📌 Neden Bu Veri Setini Seçtim?

Olist veri seti, akademik çalışmalar ve data analytics projeleri için oldukça değerli bir kaynaktır. Bu veri setini seçmemin temel nedenleri:

- **Gerçek dünya verisi olması:**  
  Siparişten teslimata, müşteri yorumlarından ödeme yöntemlerine kadar gerçek operasyon süreçlerini yansıtır.

- **Uçtan uca e-ticaret sürecini kapsaması:**  
  Tek bir veri kaynağında müşteri, ürün, sipariş, kargo, ödeme ve değerlendirme bilgileri birlikte gelir.  
  Bu da karmaşık iş süreçlerini bütünsel olarak analiz etmeyi mümkün kılar.

- **Zengin veri ilişkileri sunması:**  
  7 farklı tablo arasında çok sayıda ilişki bulunur (join yapıları).  
  Bu da hem veri modelleme hem de analitik becerilerin gelişmesi için ideal bir ortam sağlar.

- **İstatistiksel testlere uygun geniş hacimli veri:**  
  100.000’e yakın sipariş ve 71.000 müşteri bilgisiyle güvenilir hipotez testleri yapılabilir.

- **Sektör karşılığı yüksek olması:**  
  E-ticaret sektörü, veri analitiğinin en yoğun kullanıldığı alanlardan biridir.  
  Bu veri seti, gerçek iş dünyasında karşılaşılan problemlerin küçük bir simülasyonunu sunar.

Bu nedenlerle bu veri seti, hem öğrenme hem de uygulama açısından çok yüksek değer sağlamaktadır.

---

### 🛠️ Projede Kullanılan Araçlar ve Yöntemler

Bu projede veri ön işleme, istatistiksel testler ve görselleştirmeler için çeşitli modern veri bilimi araçları kullanılmıştır:

#### 🔹 Programlama Dili
- **Python (Google Colab)**  
  Pandas, NumPy, SciPy, Plotly, Matplotlib gibi analiz kütüphaneleri ile çalışılmıştır.

#### 🔹 Veri Temizleme ve Keşfi
- Eksik veri analizi  
- Veri tiplerinin dönüştürülmesi  
- Join operasyonları  
- Tanımlayıcı istatistikler  
- Outlier inceleme

#### 🔹 Görselleştirme
- **Plotly Express** ile interaktif grafikler  
- Histogram, bar chart, boxplot ve dağılım grafikleri

#### 🔹 İstatistiksel Analiz / A-B Testleri
- **Bağımsız örneklem T-testi** (teslimat süresi → memnuniyet)  
- **Tek yönlü ANOVA** (kategori → sipariş değeri)  
- **Ki-Kare testi** (ödeme yöntemi → teslim edilme durumu)

#### 🔹 Araştırma Odaklı Yaklaşım
Her analiz adımı, iş sorularına yanıt bulmak için tasarlanmış ve sonuçlar iş değeri üretecek şekilde yorumlanmıştır.


### 📊 Veri Setinin Teknik Özeti

Olist E-Ticaret veri seti, 2016–2018 yılları arasında gerçekleşen Brezilya’daki online alışveriş faaliyetlerini içeren çok boyutlu bir veri kaynağıdır. Veri seti toplam **7 ana tablodan** oluşmaktadır:

| Tablo Adı              | Açıklama                                   | Satır Sayısı |
|-----------------------|---------------------------------------------|--------------|
| orders                | Siparişlerin zaman, durum ve teslim bilgileri | ~100k        |
| customers             | Müşteri kimlik ve konum bilgileri           | ~99k         |
| order_items           | Sipariş satırları (ürün başına detay)       | ~112k        |
| payments              | Ödeme yöntemleri ve taksit bilgileri        | ~103k        |
| reviews               | Müşteri yorum ve puanlamaları               | ~99k         |
| products              | Ürün özellikleri ve kategoriler             | ~32k         |
| sellers               | Satıcı bilgileri ve konum verisi            | ~3.1k        |

Bu yapı sayesinde veri seti, gerçek bir e-ticaret platformunun uçtan uca davranışını modellemek için ideal bir temel sunar. Tablolar arasında **order_id**, **customer_id**, **product_id** ve **seller_id** gibi anahtar alanlarla güçlü ilişkiler bulunmaktadır.
